In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

MEAO = pd.read_excel('G:\Priyabrata\ML\Material data repository.xlsx')
INPUT=MEAO.iloc[:,2:11]  #all INPUT (Variables)
TARGET=MEAO.iloc[:,20]   #all PHASES SS,SS+IM,AM
#TARGET = MEAO.iloc[:,19]

Y=MEAO.iloc[:,22] #coded phases. 0:SS, 1:SS+IM, 2:AM
#Y = MEAO.iloc[:,23] #coded phases. 0:MSS, 1:SSS, 2:SS+IM, 3:AM


selected_INPUT = INPUT.drop(['Mixing entropy','Gamma','VEC','Pauling electronegativity','Molar volume dispersity'],axis=1)
selected_INPUT

normalized_INPUT=(selected_INPUT-selected_INPUT.mean())/selected_INPUT.std()

In [6]:
#ANN classifier for supervised learning
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn import metrics

X_train, X_test, y_train, y_test = train_test_split(normalized_INPUT, Y, test_size = 0.3)  #test data size is 30% of total size. #principalDataframe contains 3 PCs and Y contains coded phases (0:SS, 1:SS+IM, 2:AM)

ann = MLPClassifier(max_iter=1500)
ann.fit(X_train,y_train)
pred_ann=ann.predict(X_test)

# Predictions and Evaluations
from sklearn.metrics import classification_report, confusion_matrix
print(confusion_matrix(y_test, pred_ann))

print(classification_report(y_test, pred_ann))

metrics.accuracy_score(y_test, pred_ann)    

[[41  4  0]
 [ 6 10  1]
 [ 0  2  7]]
              precision    recall  f1-score   support

           0       0.87      0.91      0.89        45
           1       0.62      0.59      0.61        17
           2       0.88      0.78      0.82         9

    accuracy                           0.82        71
   macro avg       0.79      0.76      0.77        71
weighted avg       0.81      0.82      0.81        71



0.8169014084507042

In [7]:
#Stratified k fold cross validation (for imbalanced datasets)
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import StratifiedKFold
from numpy import mean
from numpy import std
from sklearn.model_selection import cross_val_score

skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=1)
model = MLPClassifier()
# evaluate model
scores = cross_val_score(model, normalized_INPUT, Y, scoring='accuracy', cv=skf, n_jobs=-1)
scores
# report performance
print('Accuracy: %.3f (%.3f)' % (mean(scores), std(scores)))

Accuracy: 0.872 (0.043)


In [8]:
#Repeated Stratified k fold cross validation (for imbalanced datasets)
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import RepeatedStratifiedKFold
from numpy import mean
from numpy import std
from sklearn.model_selection import cross_val_score

nskf = RepeatedStratifiedKFold(n_splits=5, n_repeats=5, random_state=1)
model = MLPClassifier()
# evaluate model
scores = cross_val_score(model, normalized_INPUT, Y, scoring='accuracy', cv=nskf, n_jobs=-1)
scores
# report performance
print('Accuracy: %.3f (%.3f)' % (mean(scores), std(scores)))



Accuracy: 0.874 (0.031)


In [9]:
#GridsearchCV to create better ANN model
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.neural_network import MLPClassifier
from sklearn import metrics


params_ann = {'hidden_layer_sizes':[(5,),(10,),(20,),(30,),(40,),(50,), (5,5),(10,10),(20,20),(30,30),(40,40),(50,50)],'solver': ['sgd', 'adam','lbfgs'],'activation': ['identity', 'logistic', 'tanh', 'relu'], 'learning_rate_init':[0.01,0.05,0.1,0.15,0.2],'warm_start':['True','False']}
ann_grid = GridSearchCV(MLPClassifier(solver='adam', max_iter=15000), param_grid=params_ann,verbose=10, cv=nskf)
#X_train, X_test, y_train, y_test = train_test_split(normalized_INPUT, Y, test_size = 0.30)  #test data size is 30% of total size. #principalDataframe contains 3 PCs and Y contains coded phases (0:SS, 1:SS+IM, 2:AM)
ann_grid.fit(X_train,y_train)
ann_grid.best_params_
ann_pred2 = ann_grid.predict(X_test)
metrics.accuracy_score(y_test,ann_pred2)

Fitting 25 folds for each of 480 candidates, totalling 12000 fits
[CV] activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True 
[CV]  activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True, score=0.909, total=   0.2s
[CV] activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True 


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s remaining:    0.0s


[CV]  activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True, score=0.939, total=   0.1s
[CV] activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True 
[CV]  activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True, score=0.879, total=   0.1s
[CV] activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True 


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.3s remaining:    0.0s


[CV]  activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True, score=0.909, total=   0.2s
[CV] activation=identity, batch_size=10, hidden_layer_sizes=30, learning_rate_init=0.01, warm_start=True 


...

[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True, score=0.879, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True, score=0.875, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True, score=0.939, total=   0.0s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True, score=0.788, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=True 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_ra

[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False, score=0.848, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False, score=0.818, total=   0.0s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False, score=0.812, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False, score=0.909, total=   0.0s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.15, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, lea

[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False, score=0.844, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False, score=0.879, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False, score=0.758, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False, score=0.879, total=   0.1s
[CV] activation=relu, batch_size=50, hidden_layer_sizes=30, learning_rate_init=0.2, warm_start=False 
[CV]  activation=relu, batch_size=50, hidden_layer_sizes=30, learning_ra

[Parallel(n_jobs=1)]: Done 12000 out of 12000 | elapsed: 27.4min finished


0.8169014084507042

In [19]:
#RandomsearchCV to create better ANN model
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import uniform
from sklearn.neural_network import MLPClassifier
from sklearn import metrics
from scipy.stats import randint as sp_randint

params_ann_RS = {'hidden_layer_sizes':[(20,), (50,100,50), (100,)],'solver': ['sgd', 'adam','lbfgs'],'activation': ['identity', 'logistic', 'tanh', 'relu'],'batch_size': sp_randint(10,50),'learning_rate_init':uniform(0.05,0.2),'warm_start':['True','False']}
ANN_RS = RandomizedSearchCV(MLPClassifier(max_iter=15000), param_distributions=params_ann_RS,n_iter=1000,verbose=10, cv=10)
ANN_RS.fit(X_train,y_train)
ANN_RS.best_params_  

Fitting 10 folds for each of 1000 candidates, totalling 10000 fits
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.941, total=   0.0s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.824, total=   0.2s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s


[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.824, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.824, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.812, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.4s remaining:    0.0s


[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.875, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=0.938, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 
[CV]  activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False, score=1.000, total=   0.1s
[CV] activation=relu, batch_size=20, hidden_layer_sizes=20, learning_rate_init=0.22962293412823115, solver=adam, warm_start=False 


...

[CV]  activation=tanh, batch_size=48, hidden_layer_sizes=20, learning_rate_init=0.05293714620898282, solver=adam, warm_start=False, score=0.875, total=   0.0s
[CV] activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True 
[CV]  activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True, score=0.882, total=   0.1s
[CV] activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True 
[CV]  activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True, score=0.824, total=   0.1s
[CV] activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True 
[CV]  activation=relu, batch_size=19, hidden_layer_sizes=20, learning_rate_init=0.08236846514142435, solver=adam, warm_start=True, scor

[CV]  activation=relu, batch_size=18, hidden_layer_sizes=20, learning_rate_init=0.09051562311710969, solver=sgd, warm_start=False, score=0.938, total=   0.2s
[CV] activation=relu, batch_size=18, hidden_layer_sizes=20, learning_rate_init=0.09051562311710969, solver=sgd, warm_start=False 
[CV]  activation=relu, batch_size=18, hidden_layer_sizes=20, learning_rate_init=0.09051562311710969, solver=sgd, warm_start=False, score=0.875, total=   0.2s
[CV] activation=tanh, batch_size=34, hidden_layer_sizes=20, learning_rate_init=0.1700102229120351, solver=adam, warm_start=False 
[CV]  activation=tanh, batch_size=34, hidden_layer_sizes=20, learning_rate_init=0.1700102229120351, solver=adam, warm_start=False, score=0.882, total=   0.1s
[CV] activation=tanh, batch_size=34, hidden_layer_sizes=20, learning_rate_init=0.1700102229120351, solver=adam, warm_start=False 
[CV]  activation=tanh, batch_size=34, hidden_layer_sizes=20, learning_rate_init=0.1700102229120351, solver=adam, warm_start=False, score

[CV]  activation=relu, batch_size=18, hidden_layer_sizes=20, learning_rate_init=0.19919564928626526, solver=adam, warm_start=True, score=0.875, total=   0.1s


[Parallel(n_jobs=1)]: Done 10000 out of 10000 | elapsed: 22.3min finished


{'activation': 'logistic',
 'batch_size': 23,
 'hidden_layer_sizes': 20,
 'learning_rate_init': 0.09337999451705328,
 'solver': 'adam',
 'warm_start': 'True'}

In [20]:
ann_pred_RS = ANN_RS.predict(X_test)
metrics.accuracy_score(y_test,ann_pred_RS)

0.8309859154929577

In [21]:
model = ANN_RS
# evaluate model
scores = cross_val_score(model, normalized_INPUT, Y, scoring='accuracy', cv=nskf,verbose=10, n_jobs=-1)
scores
# report performance
print('Accuracy: %.3f (%.3f)' % (mean(scores), std(scores)))

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 tasks      | elapsed: 49.5min
[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed: 106.3min
[Parallel(n_jobs=-1)]: Done  13 out of  25 | elapsed: 127.6min remaining: 117.8min
[Parallel(n_jobs=-1)]: Done  16 out of  25 | elapsed: 199.3min remaining: 112.1min
[Parallel(n_jobs=-1)]: Done  19 out of  25 | elapsed: 249.2min remaining: 78.7min
[Parallel(n_jobs=-1)]: Done  22 out of  25 | elapsed: 259.9min remaining: 35.4min


Accuracy: 0.889 (0.038)


[Parallel(n_jobs=-1)]: Done  25 out of  25 | elapsed: 302.6min finished
[Parallel(n_jobs=-1)]: Done  25 out of  25 | elapsed: 302.6min remaining:    0.0s


In [16]:
model.best_params_ 

{'activation': 'logistic',
 'batch_size': 27,
 'hidden_layer_sizes': 20,
 'learning_rate_init': 0.16815167775079365,
 'warm_start': 'True'}